# Download and Install Devito

There are two main approaches to installing Devito.

-   `Docker`, for those looking for the least-friction way to try Devito
-   `Virtual environment`, for those looking to use Devito as part of a
    project alongside other packages

## Docker

### [Devito](https://github.com/devitocodes/devito) Docker image library

In order to facilitate the dissemination, usage, and development of
Devito, we provide a series of Docker images. These images support
numerous architectures and compilers and are tagged accordingly. You can
find all the available images at
[DevitoHub](https://hub.docker.com/r/devitocodes/). The following
describes the available images and the workflow to build it yourself.

#### [Devito](https://github.com/devitocodes/devito) images

Devito provides several images that target different architectures and
compilers. In the following, all images are described as `imagename-*`.
The `*` corresponds to, and should be swapped for, the different release
tags `dev`, `latest` or `vx.x.x` depending on if you are interested in
specific versions (`vx.x.x`), the latest stable release(`latest`), or
the latest development status (`dev`).

#### [Devito](https://github.com/devitocodes/devito) on CPU

We provide two CPU images: - `devito:gcc-*` with the standard GNU gcc
compiler. - `devito:icx-*` with the Intel C compiler for Intel
architectures.

These images provide a working environment for any CPU architecture and
come with [Devito](https://github.com/devitocodes/devito), `gcc/icx` and
`mpi` preinstalled, and utilities such as `jupyter` for usability and
exploration of the package.

To run this image locally, you will first need to install `docker`.
Then, the following commands will get you started:

``` bash
# Pull image and start a bash shell 
docker run --rm -it -p 8888:8888 -p 8787:8787 -p 8786:8786 devitocodes/devito:gcc-latest /bin/bash
docker run --rm -it -p 8888:8888 -p 8787:8787 -p 8786:8786 --device=/dev/infiniband/uverbs0 --device=/dev/infiniband/rdma_cm devitocodes/devito:gcc-latest /bin/bash

# or start a Jupyter notebook server on port 8888
docker run --rm -it -p 8888:8888 devitocodes/devito:gcc-latest
```

Alternatively, to run in user context on a cluster with a shared
filesystem, you can add the correct user config as `docker` options,
e.g.:

``` bash
docker run --rm -it -v `pwd`:`pwd` -w `pwd` -u $(id -u):$(id -g) devitocodes/devito:gcc-latest python examples/seismic/acoustic/acoustic_example.py
```

**Notes**: In addition, the following legacy tags are available:

-   `devito:cpu-*` that corresponds to `devito:gcc-*`

#### [Devito](https://github.com/devitocodes/devito) on GPU

Second, we provide three images to run
[Devito](https://github.com/devitocodes/devito) on GPUs, tagged
`devito:nvidia-nvc-*`, and `devito:amd-*`.

-   `devito:nvidia-nvc-*` is intended to be used on NVidia GPUs. It
    comes with the configuration to use the `nvc` compiler for `openacc`
    offloading. This image also comes with CUDA-aware MPI for multi-GPU
    deployment.
-   `devito:amd-*` is intended to be used on AMD GPUs. It comes with the
    configuration to use the `aoompcc` compiler for `openmp` offloading.
    This image also comes with ROCm-aware MPI for multi-GPU deployment.
    This image can also be used on AMD CPUs since the ROCm compilers are
    preinstalled.

##### NVidia

To run the NVidia GPU version, you will need
[nvidia-docker](https://github.com/NVIDIA/nvidia-docker) installed and
to specify the GPUs to use at runtime with the `--gpus` flag. See, for
example, a few runtime commands for the NVidia `nvc` images.

``` bash
docker run --gpus all --rm -it -p 8888:8888 -p 8787:8787 -p 8786:8786 devitocodes/devito:nvidia-nvc-latest
docker run --gpus all --rm -it devitocodes/devito:nvidia-nvc-latest python examples/seismic/acoustic/acoustic_example.py

docker run --gpus all --rm -it -p 8888:8888 -p 8787:8787 -p 8786:8786 --device=/dev/infiniband/uverbs0 --device=/dev/infiniband/rdma_cm  devitocodes/devito:nvidia-nvc-latest
```

or to run in user context on a cluster with a shared filesystem, you can
add the correct user config as `docker` options, e.g.:

``` bash
docker run --gpus all --rm -it -v `pwd`:`pwd` -w `pwd` -u $(id -u):$(id -g) devitocodes/devito:nvidia-nvc-latest python examples/seismic/acoustic/acoustic_example.py
```

##### AMD

Unlike NVidia, AMD does not require an additional Docker setup and runs
with the standard docker. You will, however, need to pass some flags so
that the image is linked to the GPU devices. You can find a short
walkthrough in these [AMD
notes](https://developer.amd.com/wp-content/resources/ROCm%20Learning%20Centre/chapter5/Chapter5.3_%20KerasMultiGPU_ROCm.pdf)
for their TensorFlow GPU Docker image.

**Notes**: In addition, the following legacy tags are available:

-   `devito:gpu-*` that corresponds to `devito:nvidia-nvc-*`

### Build a [Devito](https://github.com/devitocodes/devito) image

To build the images yourself, you only need to run the standard build
command using the provided Dockerfile. The main difference between the
CPU and GPU images will be the base image used.

To build the (default) CPU image, run:

``` bash
docker build --network=host --file docker/Dockerfile.devito --tag devito .
```

To build the GPU image with `openacc` offloading and the `nvc` compiler,
run:

``` bash
docker build --build-arg base=devitocodes/bases:nvidia-nvc --network=host --file docker/Dockerfile.devito --tag devito .
```

or if you wish to use the `amdclang` compiler with `openmp` offloading
for AMD architectures:

``` bash
docker build --build-arg base=devitocodes/bases:amd --network=host --file docker/Dockerfile --tag devito .
```

### Debugging a base image

To build the base image yourself locally, you need to run the standard
build command using the provided Dockerfile. Following this, we build
the Devito image using the previously built base:

``` bash
docker build . --file docker/Dockerfile.cpu --tag devito-gcc --build-arg arch=gcc
docker build . --file docker/Dockerfile.devito --tag devito_img --build-arg base=devito-gcc:latest
```

and then, to run tests or/and examples using the newly built image

``` bash
docker run --rm --name testrun devito_img pytest -k "not adjoint" -m "not parallel" tests/
docker run --rm --name testrun devito_img py.test --nbval -k 'not dask' examples/seismic/tutorials/
```

### Developing Devito with Docker

For those aiming to develop in Devito using Docker, you can use
docker-compose. We start by cloning the repo and entering the Devito
directory.

``` bash
git clone https://github.com/devitocodes/devito.git
cd devito
```

#### Example CPU

``` bash
# Start a terminal to develop/run for CPUs using docker compose
docker-compose run devito /bin/bash
```

#### Example GPU

``` bash
# Start a terminal to develop/run for GPUs using docker compose
docker-compose run devito.nvidia /bin/bash
```

## Virtual environment

### venv route

Devito is available as a `pip package` in PyPI.

Create a [Python virtual
environment](https://docs.python.org/3/library/venv.html)

``` bash
python3 -m venv <your_venv_name>
```

Source the newly created `venv`. This needs to be repeated each time a
new terminal is open.

``` bash
source <your_venv_name>/bin/activate
```

To install the `latest Devito release` along with any additional
dependencies, follow:

``` bash
   pip install devito
   # ...or to install additional dependencies:
   # pip install devito[extras,mpi,nvidia,tests]
```

[latest Devito release](https://pypi.org/project/devito/#history)

To install the latest Devito development version, without the tutorials,
follow:

``` bash
pip install git+https://github.com/devitocodes/devito.git
# ...or to install additional dependencies:
# pip install devito[tests,extras,mpi] @ git+https://github.com/devitocodes/devito@master
```

Additional dependencies:

-   extras : optional dependencies for Jupyter notebooks, plotting,
    benchmarking
-   tests : optional dependencies required for testing infrastructure
-   mpi : optional dependencies for MPI (mpi4py)
-   nvidia : optional dependencies for targetting GPU deployment

[pip package](https://pypi.org/project/devito/)

Note that here, you do not need to get the code via `git clone`.
Depending on your needs, this might also be the recommended setup for
using Devito in a production-like environment. However, since some
components need to be compiled before use, this approach may be
sensitive to the C/C++ compilers present on your system and the related
environment, including what other packages you might have installed.

### conda route

Please install either [Anaconda](https://www.continuum.io/downloads) or
[Miniconda](https://conda.io/miniconda.html). Once install, you can
create a virtual environment with eithera [Python virtual
environment](https://docs.python.org/3/library/venv.html) or a [Conda
environment](https://docs.conda.io/projects/conda/en/latest/user-guide/concepts/environments.html):

``` bash
# Create new env with the name devito
conda create --name devito
# Activate the environment
conda activate devito
```

and finally, install Devito along with any extra dependencies:

``` bash
pip install devito
# ... or to install additional dependencies
# pip install devito[extras,mpi,nvidia,tests]
```

### For developers

First clone Devito:

``` bash
git clone https://github.com/devitocodes/devito.git
cd devito
```

and then install the requirements in your virtual environment (venv or
conda):

``` bash
# Install requirements
pip install -e .
# ...or to install additional dependencies
# pip install -e .[extras,mpi,nvidia,tests]
```

### Facing issues

If you are facing any issues, we are happy to help on Slack\_. Also,
have a look at our list of known [installation
issues](https://github.com/devitocodes/devito/wiki/Installation-Issues)
or join us on
[Slack](https://join.slack.com/t/devitocodes/shared_invite/zt-2hgp6891e-jQDcepOWPQwxL5JJegYKSA)
to interact with the developers and the community.